In [27]:
import pandas as pd
from datetime import datetime, timedelta


In [28]:
def load_data(file_path):
    """Load data from the station file."""
    df = pd.read_csv(
        file_path,
        delim_whitespace=True,
        names=["year", "month", "day", "hour", "temp", "pressure"],
        skiprows=1  # Skip the header row in the file
    )
    # Combine columns into a single datetime index
    df['datetime'] = pd.to_datetime(df[['year', 'month', 'day', 'hour']])
    df = df.set_index('datetime')
    return df[['temp', 'pressure']]

In [31]:
def get_ecmwf_atm_cond(station_code, starttime, endtime):
    """
    Reads atmospheric conditions at a station (6h data from ECMWF) and returns T and P within a given time range.
    Parameters:
        station_code (str): Station code, e.g., "NO0002R"
        starttime (str): Start time of time range, e.g., "1971-01-01T13:00Z"
        endtime (str): End time of time range, e.g., "1971-01-01T14:00Z"  
    Returns:
        average_temp and average_pressure within the specified time range.
    """
    # Parse times and remove timezone awareness
    starttime = pd.to_datetime(starttime).tz_convert(None)
    endtime = pd.to_datetime(endtime).tz_convert(None)
    
    # Load data
    #path = '/xnilu_wrk/users/.../data/'  # Path to the data files
    #file_path = f"{path}{station_code}.txt"  # File is named after the station code 
    file_path = f"{station_code}.txt"  # File is named after the station code 
    data = load_data(file_path)
    
    # Extract data within the range
    data_in_range = data[starttime:endtime]

    #print(data_in_range)
    
    if data_in_range.empty:
        # If no data points are within range, interpolate between nearest neighbors
        before_start = data[data.index < starttime].iloc[-1]
        after_start = data[data.index >= starttime].iloc[0]
        time_fraction = (starttime - before_start.name) / (after_start.name - before_start.name)
        
        temp_interp = before_start['temp'] + time_fraction * (after_start['temp'] - before_start['temp'])
        pressure_interp = before_start['pressure'] + time_fraction * (after_start['pressure'] - before_start['pressure'])
        
        return temp_interp, pressure_interp
    
    elif len(data_in_range) == 1:
        # If there's only one data point, return it as it is
        return data_in_range['temp'].iloc[0], data_in_range['pressure'].iloc[0]
    
    else:
        # Average temperature and pressure over the specified range
        average_temp = data_in_range['temp'].mean()
        average_pressure = data_in_range['pressure'].mean()
        
        return average_temp, average_pressure

In [30]:
# Example
station_code = "NO0002R"

starttime = "1971-01-01T13:00Z"
endtime = "1971-01-01T14:00Z"
temp1, pressure1 = get_ecmwf_atm_cond(station_code, starttime, endtime)
print(f"Temperature: {temp1:.1f}, Pressure: {pressure1:.1f}")

starttime = "2010-01-01T07:01Z"
endtime = "2010-01-02T07:01Z"
temp2, pressure2 = get_ecmwf_atm_cond(station_code, starttime, endtime)
print(f"Temperature: {temp2:.1f}, Pressure: {pressure2:.1f}")


Temperature: 272.0, Pressure: 99426.5
Temperature: 269.5, Pressure: 99256.3
